In [ ]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


In [ ]:
pip install datasets

In [ ]:
pip install transformers

In [ ]:
pip install GPUtil 

In [ ]:
# reference - https://towardsdatascience.com/text-classification-with-cnns-in-pytorch-1113df31e79f

In [ ]:
# modules
import pandas as pd
import os
from datetime import datetime
import matplotlib.pyplot as plt
import seaborn as sns
from nltk.tokenize import TweetTokenizer
from nltk.corpus import stopwords
import tqdm
import numpy as np
from numpy import mean
from numpy import std
from datasets import load_metric
import random
from IPython.display import FileLink, FileLinks

import torch
from torch.utils.data import DataLoader, RandomSampler, TensorDataset

import tensorflow as tf
from tensorflow.keras import regularizers
from tensorflow.keras.optimizers import Adam, SGD
from transformers import pipeline

import transformers
from transformers import AutoModelForSequenceClassification, TrainingArguments, Trainer, AutoTokenizer, AutoModel, BertTokenizer, BertModel
from sklearn.model_selection import KFold
import gc
from GPUtil import showUtilization as gpu_usage

In [ ]:
pip install transformers

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     |████████████████████████████████| 5.5 MB 32.3 MB/s 
     |████████████████████████████████| 7.6 MB 62.3 MB/s 
     |████████████████████████████████| 182 kB 73.1 MB/s 


In [ ]:
from transformers import AutoTokenizer, AutoModel
import random, math
from typing import Union
import numpy as np
import torch
from torch import Tensor
import torch.nn as nn
import torch.nn.functional as F
from torch.utils.data import DataLoader
from tqdm.auto import tqdm
import transformers
from sklearn.model_selection import cross_validate
from sklearn.model_selection import KFold 
from sklearn.metrics import accuracy_score, f1_score, precision_score, recall_score

def load_datasets() -> Union[dict, dict]:

    import json
    import os
    
    train = {}
    test = {}

    train_df = pd.read_csv(r'/content/drive/MyDrive/dreaddit/dreaddit-train.csv')
    test_df = pd.read_csv(r'/content/drive/MyDrive/dreaddit/dreaddit-test.csv')
        
    train["texts"] = train_df.text.tolist() 
    train["label"] = train_df.label.tolist() 

    test["texts"] = test_df.text.tolist()
    test["label"] = test_df.label.tolist()
    
    return train, test



# K-Fold Cross-Validation
def cross_validation(model, _X, _y, _cv=5):

      '''Function to perform 5 Folds Cross-Validation
       Parameters
       ----------
      model: Python Class, default=None
              This is the machine learning algorithm to be used for training.
      _X: array
           This is the matrix of features.
      _y: array
           This is the target variable.
      _cv: int, default=5
          Determines the number of folds for cross-validation.
       Returns
       -------
       The function returns a dictionary containing the metrics 'accuracy', 'precision',
       'recall', 'f1' for both training set and validation set.
      '''
      _scoring = ['accuracy', 'precision', 'recall', 'f1']
      results = cross_validate(estimator=model,
                               X=_X,
                               y=_y,
                               cv=_cv,
                               scoring=_scoring,
                               return_train_score=True)
      
      return {"Training Accuracy scores": results['train_accuracy'],
              "Mean Training Accuracy": results['train_accuracy'].mean()*100,
              "Training Precision scores": results['train_precision'],
              "Mean Training Precision": results['train_precision'].mean(),
              "Training Recall scores": results['train_recall'],
              "Mean Training Recall": results['train_recall'].mean(),
              "Training F1 scores": results['train_f1'],
              "Mean Training F1 Score": results['train_f1'].mean(),
              "Validation Accuracy scores": results['test_accuracy'],
              "Mean Validation Accuracy": results['test_accuracy'].mean()*100,
              "Validation Precision scores": results['test_precision'],
              "Mean Validation Precision": results['test_precision'].mean(),
              "Validation Recall scores": results['test_recall'],
              "Mean Validation Recall": results['test_recall'].mean(),
              "Validation F1 scores": results['test_f1'],
              "Mean Validation F1 Score": results['test_f1'].mean()
              }


class Dataset(torch.utils.data.Dataset):
    def __init__(self, data_dict: dict):
        self.data_dict = data_dict
        dd = data_dict

    def __len__(self):
        return len(self.data_dict["texts"])

    def __getitem__(self, idx):
        dd = self.data_dict
        return dd["texts"][idx], dd["label"][idx]


def train_CNN(model, loader, device):
    model.train()
    criterion = model.get_criterion()
    total_loss = 0.0
    
    for X,y in tqdm(loader):
        print(len(X))
        optimizer.zero_grad()

        inputs = model.embedding(X).to(device)
        target = y.to(device, dtype=torch.float32)

        pred = model(inputs)

        # loss = criterion(pred, target)
        loss = F.binary_cross_entropy(pred, target)
        loss.backward()
        optimizer.step()

        total_loss += loss.item()

    return total_loss / len(loader)

@torch.no_grad()
def eval_mentalbert(model, loader, device):
    model.eval()

    targets = []
    preds = []
    for X,y in tqdm(loader):
        print(len(X))
        optimizer.zero_grad()

        inputs = model.embedding(X).to(device)
        target = y.to(device, dtype=torch.float32)

        pred = model(inputs)

        preds.append(pred)
        targets.append(target)

    return torch.cat(preds), torch.cat(targets)

class ConvNeuralNet(nn.Module):
	#  Determine what layers and their order in CNN object 
    def __init__(self):
        super(ConvNeuralNet, self).__init__()
        
        self.tokenizer = AutoTokenizer.from_pretrained("mental/mental-bert-base-uncased")
        self.pretrained_model = AutoModel.from_pretrained("mental/mental-bert-base-uncased")

        # Parameters regarding text preprocessing
        self.seq_len = 100
        self.num_words = 50000
        self.embedding_size = 768
        
        # Dropout definition
        self.dropout = nn.Dropout(0.25)
        
        # CNN parameters definition
        # Kernel sizes
        self.kernel_1 = 2
        self.kernel_2 = 3
        self.kernel_3 = 4
        self.kernel_4 = 5
        
        # Output size for each convolution
        self.out_size = 768
        # Number of strides for each convolution
        self.stride = 1
        
        # Embedding layer definition
        self.embedding = nn.Embedding(self.num_words + 1, self.embedding_size, padding_idx=0)
        
        # Convolution layers definition
        self.conv_1 = nn.Conv1d(self.seq_len, self.out_size, self.kernel_1, self.stride)
        self.conv_2 = nn.Conv1d(self.seq_len, self.out_size, self.kernel_2, self.stride)
        self.conv_3 = nn.Conv1d(self.seq_len, self.out_size, self.kernel_3, self.stride)
        self.conv_4 = nn.Conv1d(self.seq_len, self.out_size, self.kernel_4, self.stride)
        
        # Max pooling layers definition
        self.pool_1 = nn.MaxPool1d(self.kernel_1, self.stride)
        self.pool_2 = nn.MaxPool1d(self.kernel_2, self.stride)
        self.pool_3 = nn.MaxPool1d(self.kernel_3, self.stride)
        self.pool_4 = nn.MaxPool1d(self.kernel_4, self.stride)
        
        # Fully connected layer definition
        self.fc = nn.Linear(self.in_features_fc(), 1)
    
        
        self.criterion = nn.CrossEntropyLoss()
        
        
    def get_pretrained_model(self):
        return self.pretrained_model

    def get_tokenizer(self):
        return self.tokenizer
    
    def get_criterion(self):
        return self.criterion

    def assign_optimizer(self, lr=0.0001, weight_decay = 0.005, momentum = 0.9):
        optimizer = torch.optim.SGD(model.parameters(), lr=0.0001, weight_decay = 0.005, momentum = 0.9)
        return optimizer

    def tokenize(
                self,
                texts: "list[str]",
                max_length: int = 100,
                truncation: bool = True,
                padding: bool = True,
            ):
                
                tokenizer = self.get_tokenizer()
                # print('------->>>',list(texts))

                tokenized = tokenizer(list(texts), 
                                        max_length = max_length, 
                                        truncation = True, 
                                        padding = True,
                                        return_tensors ="pt")
        
                return tokenized        


    def embedding(self, inputs):
        Model = self.get_pretrained_model()
        encoded_input = self.tokenize(inputs)
        # for t in encoded_input:
        # print('------->>>',encoded_input['input_ids'].shape)
        Model.eval()
        # sentence_embeddings = []
        with torch.no_grad():
                model_output_train = Model(**encoded_input.to(device))
                hid_states = model_output_train[0]
                # print('------->>>',hid_states.shape)
                # tok_vecs = hid_states[-2]
                # print(tok_vecs.shape)
                # sentence_embeddings.extend(torch.mean(tok_vecs,dim=1))
        # print(len(sentence_embeddings))
        return hid_states.to(device)
    
    # Progresses data across layers    
   
    
    def in_features_fc(self):
          '''Calculates the number of output features after Convolution + Max pooling
             
          Convolved_Features = ((embedding_size + (2 * padding) - dilation * (kernel - 1) - 1) / stride) + 1
          Pooled_Features = ((embedding_size + (2 * padding) - dilation * (kernel - 1) - 1) / stride) + 1
          
          source: https://pytorch.org/docs/stable/generated/torch.nn.Conv1d.html
          '''
          # Calcualte size of convolved/pooled features for convolution_1/max_pooling_1 features
          out_conv_1 = ((self.embedding_size - 1 * (self.kernel_1 - 1) - 1) / self.stride) + 1
          out_conv_1 = math.floor(out_conv_1)
          out_pool_1 = ((out_conv_1 - 1 * (self.kernel_1 - 1) - 1) / self.stride) + 1
          out_pool_1 = math.floor(out_pool_1)
          
          # Calcualte size of convolved/pooled features for convolution_2/max_pooling_2 features
          out_conv_2 = ((self.embedding_size - 1 * (self.kernel_2 - 1) - 1) / self.stride) + 1
          out_conv_2 = math.floor(out_conv_2)
          out_pool_2 = ((out_conv_2 - 1 * (self.kernel_2 - 1) - 1) / self.stride) + 1
          out_pool_2 = math.floor(out_pool_2)
          
          # Calcualte size of convolved/pooled features for convolution_3/max_pooling_3 features
          out_conv_3 = ((self.embedding_size - 1 * (self.kernel_3 - 1) - 1) / self.stride) + 1
          out_conv_3 = math.floor(out_conv_3)
          out_pool_3 = ((out_conv_3 - 1 * (self.kernel_3 - 1) - 1) / self.stride) + 1
          out_pool_3 = math.floor(out_pool_3)
          
          # Calcualte size of convolved/pooled features for convolution_4/max_pooling_4 features
          out_conv_4 = ((self.embedding_size - 1 * (self.kernel_4 - 1) - 1) / self.stride) + 1
          out_conv_4 = math.floor(out_conv_4)
          out_pool_4 = ((out_conv_4 - 1 * (self.kernel_4 - 1) - 1) / self.stride) + 1
          out_pool_4 = math.floor(out_pool_4)
          
          # Returns "flattened" vector (input for fully connected layer)
          return (out_pool_1 + out_pool_2 + out_pool_3 + out_pool_4) * self.out_size    
   
    def forward(self, x):
    
          # Sequence of tokes is filterd through an embedding layer
          # x = self.embedding(x)
          
          # Convolution layer 1 is applied
          x1 = self.conv_1(x)
          x1 = torch.relu(x1)
          x1 = self.pool_1(x1)
          
          # Convolution layer 2 is applied
          x2 = self.conv_2(x)
          x2 = torch.relu((x2))
          x2 = self.pool_2(x2)
       
          # Convolution layer 3 is applied
          x3 = self.conv_3(x)
          x3 = torch.relu(x3)
          x3 = self.pool_3(x3)
          
          # Convolution layer 4 is applied
          x4 = self.conv_4(x)
          x4 = torch.relu(x4)
          x4 = self.pool_4(x4)
          
          # The output of each convolutional layer is concatenated into a unique vector
          union = torch.cat((x1, x2, x3, x4), 2)
          union = union.reshape(union.size(0), -1)
    
          # The "flattened" vector is passed through a fully connected layer
          out = self.fc(union)
          # Dropout is applied		
          out = self.dropout(out)
          # Activation function is applied
          out = torch.sigmoid(out)
          
          return out.squeeze() 

if __name__ == "__main__":
    import pandas as pd

    random.seed(2022)
    torch.manual_seed(2022)

    sample_size = None  
    batch_size = 64
    n_epochs = 10
    num_words = 50000

    # If you use GPUs, use the code below:
    device = torch.device("cuda" if torch.cuda.is_available() else "cpu")

    train_raw, test_raw = load_datasets()
    

    if sample_size is not None:
        for key in ["texts", "label"]:
            train_raw[key] = train_raw[key][:sample_size]
            test_raw[key] = test_raw[key][:sample_size]
    
    # print(len(train_raw['texts']))
    
    print("=" * 80)
    print("Running test code for part 1")
    print("-" * 80)


    test_loader = torch.utils.data.DataLoader(
        Dataset(test_raw), batch_size=batch_size, shuffle=False
    )


    X = np.array(train_raw['texts'])
    y = np.array(train_raw['label'])

    k = 10
    kf = KFold(n_splits=k, random_state=None)
    
    acc_train = []
    pr_train = []
    re_train = []
    f1_train = []

    acc_valid = []
    pr_valid = []
    re_valid = []
    f1_valid = []
     
    f = 0
    for train_index , test_index in kf.split(X):
        f+=1
        
        train = {}
        valid = {}
        
        X_train , X_test = X[train_index], X[test_index]
        y_train , y_test = y[train_index] , y[test_index]
        
        train['texts'] = X_train.tolist()
        train['label'] = y_train.tolist()
        
        valid['texts'] = X_test.tolist()
        valid['label'] = y_test.tolist()

        train_loader = torch.utils.data.DataLoader(
            Dataset(train), batch_size=batch_size, shuffle=True
        )

        valid_loader = torch.utils.data.DataLoader(
            Dataset(valid), batch_size=batch_size, shuffle=False
        )
        
        model = ConvNeuralNet().to(device)
        optimizer = model.assign_optimizer(lr=1e-4)
        
        train_accuracies = []
        train_precisions = []
        train_recalls = []
        train_f1_scores = []

        
        valid_accuracies = []
        valid_precisions = []
        valid_recalls = []
        valid_f1_scores = []        
        
        valid_accuracies = []
        
        previous_valid_accuracy = -1
        
        for epoch in range(n_epochs):

            loss = train_CNN (model, train_loader, device=device)
    
            train_preds, train_targets = eval_mentalbert(model, train_loader, device=device)
            train_preds = train_preds.round()
            
            train_accuracy = accuracy_score(train_targets.cpu(), train_preds.cpu())
            train_accuracies.append(train_accuracy)
            train_precision = precision_score(train_targets.cpu(), train_preds.cpu())
            train_precisions.append(train_precision)
            train_recall = recall_score(train_targets.cpu(), train_preds.cpu())
            train_recalls.append(train_recall)
            train_f1 = f1_score(train_targets.cpu(), train_preds.cpu())
            train_f1_scores.append(train_f1)          
            

            eval_preds, eval_targets = eval_mentalbert(model, valid_loader, device=device)
            eval_preds = eval_preds.round()

            eval_accuracy = accuracy_score(eval_targets.cpu(), eval_preds.cpu())
            valid_accuracies.append(eval_accuracy)
            valid_precision = precision_score(eval_targets.cpu(), eval_preds.cpu())
            valid_precisions.append(valid_precision)
            valid_recall = recall_score(eval_targets.cpu(), eval_preds.cpu())
            valid_recalls.append(valid_recall)
            valid_f1_score = f1_score(eval_targets.cpu(), eval_preds.cpu())
            valid_f1_scores.append(valid_f1_score)
           
            print("Epoch:", epoch)
            print("Training loss:", loss)
            print("Train Accuracy:", train_accuracy)
            print("Validation Accuracy:", eval_accuracy)
    
            print('---'*10)   
            
            #if eval_accuracy < previous_valid_accuracy:
            #    break
            #else:
            #    previous_valid_accuracy = eval_accuracy
        
     
        acc_train.append(sum(train_accuracies)/len(train_accuracies))
        pr_train.append(sum(train_precisions)/len(train_precisions))
        re_train.append(sum(train_recalls)/len(train_recalls))
        f1_train.append(sum(train_f1_scores)/len(train_f1_scores))

        acc_valid.append(sum(valid_accuracies)/len(valid_accuracies))
        pr_valid.append(sum(valid_precisions)/len(valid_precisions))
        re_valid.append(sum(valid_recalls)/len(valid_recalls))
        f1_valid.append(sum(valid_f1_scores)/len(valid_f1_scores))
        
        print('Fold',f, '>>>...'*10)
    
    print("Total Training Accuracy:", sum(acc_train)/len(acc_train))
    print("Total Training Preciion:", sum(pr_train)/len(pr_train))
    print("Total Training Recall:", sum(re_train)/len(re_train))
    print("Total Training F1_Score:", sum(f1_train)/len(f1_train))
    
    print('>>><<<'*10)

    print("Total Validation Accuracy:", sum(acc_valid)/len(acc_valid))
    print("Total Validation Precision:", sum(pr_valid)/len(pr_valid))
    print("Total Validation Recall:", sum(re_valid)/len(re_valid))
    print("Total Validation F1_Score:", sum(f1_valid)/len(f1_valid))

    print('>>><<<'*10)
    
    test_preds, test_targets = eval_mentalbert(model, test_loader, device=device)
    test_preds = test_preds.round()

    test_accuracy = accuracy_score(test_targets.cpu(), test_preds.cpu())
    test_precision = precision_score(test_targets.cpu(), test_preds.cpu())
    test_recall = recall_score(test_targets.cpu(), test_preds.cpu())
    test_f1_score = f1_score(test_targets.cpu(), test_preds.cpu())
   
    print("Total TEST Accuracy:", test_accuracy)
    print("Total TEST Precision:", test_precision)
    print("Total TEST Recall:", test_recall)
    print("Total TEST F1_Score:", test_f1_score)


Running test code for part 1
--------------------------------------------------------------------------------


Some weights of the model checkpoint at mental/mental-bert-base-uncased were not used when initializing BertModel: ['cls.predictions.transform.dense.weight', 'cls.predictions.transform.LayerNorm.bias', 'cls.predictions.transform.LayerNorm.weight', 'cls.predictions.transform.dense.bias', 'cls.predictions.decoder.bias', 'cls.predictions.decoder.weight', 'cls.predictions.bias']
- This IS expected if you are initializing BertModel from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing BertModel from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
Some weights of BertModel were not initialized from the model checkpoint at mental/mental-bert-base-uncased and are newly initialized: ['bert.pooler.dense.bias', 'bert.p

  0%|          | 0/40 [00:00<?, ?it/s]

64
64
64
64
64
64
64
64
64
64
64
64
64
64
64
64
64
64
64
64
64
64
64
64
64
64
64
64
64
64
64
64
64
64
64
64
64
64
64
58


  0%|          | 0/40 [00:00<?, ?it/s]

...

64
64
64
64
64
64
64
64
64
64
64
64
64
64
64
64
64
64
64
64
64
64
64
64
64
64
64
64
64
64
64
64
64
64
64
64
64
64
64
59


  0%|          | 0/5 [00:00<?, ?it/s]

64
64
64
64
27
Epoch: 9
Training loss: 0.07228826014325022
Train Accuracy: 0.9980430528375733
Validation Accuracy: 0.8091872791519434
------------------------------
Fold 10 >>>...>>>...>>>...>>>...>>>...>>>...>>>...>>>...>>>...>>>...
Total Training Accuracy: 0.8133021652080232
Total Training Preciion: 0.8266327994467476
Total Training Recall: 0.9434487553600631
Total Training F1_Score: 0.8553878884837054
>>><<<>>><<<>>><<<>>><<<>>><<<>>><<<>>><<<>>><<<>>><<<>>><<<
Total Validation Accuracy: 0.6967262230627582
Total Validation Precision: 0.7198916892791158
Total Validation Recall: 0.8385343312084517
Total Validation F1_Score: 0.7408843869017463
>>><<<>>><<<>>><<<>>><<<>>><<<>>><<<>>><<<>>><<<>>><<<>>><<<


  0%|          | 0/12 [00:00<?, ?it/s]

64
64
64
64
64
64
64
64
64
64
64
11
Total TEST Accuracy: 0.7454545454545455
Total TEST Precision: 0.8213058419243986
Total TEST Recall: 0.6476964769647696
Total TEST F1_Score: 0.7242424242424242
